In [19]:
!pip install torch -U

Defaulting to user installation because normal site-packages is not writeable
  Obtaining dependency information for nvidia-nccl-cu12==2.19.3 from https://files.pythonhosted.org/packages/38/00/d0d4e48aef772ad5aebcf70b73028f88db6e5640b36c38e90445b7a57c45/nvidia_nccl_cu12-2.19.3-py3-none-manylinux1_x86_64.whl.metadata
  Using cached nvidia_nccl_cu12-2.19.3-py3-none-manylinux1_x86_64.whl.metadata (1.8 kB)
Using cached nvidia_nccl_cu12-2.19.3-py3-none-manylinux1_x86_64.whl (166.0 MB)


In [27]:
!pip install jiwer

Defaulting to user installation because normal site-packages is not writeable
  Obtaining dependency information for jiwer from https://files.pythonhosted.org/packages/0d/4f/ee537ab20144811dd99321735ff92ef2b3a3230b77ed7454bed4c44d21fc/jiwer-3.0.3-py3-none-any.whl.metadata
  Obtaining dependency information for click<9.0.0,>=8.1.3 from https://files.pythonhosted.org/packages/00/2e/d53fa4befbf2cfa713304affc7ca780ce4fc1fd8710527771b58311a3229/click-8.1.7-py3-none-any.whl.metadata
  Obtaining dependency information for rapidfuzz<4,>=3 from https://files.pythonhosted.org/packages/a3/49/6b56c6aa01f15fa682c7827c5d7432866790099a62f0f9f94e25b76283b3/rapidfuzz-3.6.2-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata
Using cached jiwer-3.0.3-py3-none-any.whl (21 kB)
Using cached click-8.1.7-py3-none-any.whl (97 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 25.4 MB/s eta 0:00:00a 0:00:01
  Consider adding this directory to PATH or, if you prefer to suppress this warni

In [4]:
from datasets import load_dataset
dataset = load_dataset('audiofolder', data_dir="/work/jh2lab/elic_model/ivn_audio_chunk", split = 'train')


Resolving data files:   0%|          | 0/1387 [00:00<?, ?it/s]

In [5]:
dataset = dataset.train_test_split(test_size=0.2)
dataset

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 1108
    })
    test: Dataset({
        features: ['audio', 'transcription'],
        num_rows: 278
    })
})

In [6]:
from datasets import Audio

dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))

In [7]:
dataset['train'][0]

{'audio': {'path': '/work/jh2lab/elic_model/ivn_audio_chunk/ivn008-2023-02-14-Rovinj_08_2_8.wav',
  'array': array([-2.21113747e-04, -1.52711145e-04,  1.51308341e-05, ...,
         -1.07557815e-03, -1.18678738e-03,  0.00000000e+00]),
  'sampling_rate': 16000},
 'transcription': "Quel go imparà a- Čr- in- de Črnja, la roba migliore che go imparà là per tuta la vita, non esisti situazion ch- iriso- irisolvibile, non esisti, neanche una. Tuto se risolvi. Tuto. E il me ga imparà @ 'sto capo che xe mato, però xe bravissimo, sempre gaver tre-quatro @ piani."}

In [8]:

# data augmentation
from audiomentations import Compose, AddGaussianNoise, TimeStretch, PitchShift, Shift

augment_waveform = Compose([
    AddGaussianNoise(min_amplitude=0.005, max_amplitude=0.015, p=0.2),
    TimeStretch(min_rate=0.8, max_rate=1.25, p=0.2, leave_length_unchanged=False),
    PitchShift(min_semitones=-4, max_semitones=4, p=0.2)
    ,])


def augment_dataset(batch):

    audio = batch["audio"]["array"]
    # apply augmentation
    augmented_audio = augment_waveform(samples=audio, sample_rate=16000)

    batch["audio"]["array"] = augmented_audio


    return batch


In [9]:
dataset["train"] = dataset["train"].map(augment_dataset)


Map:   0%|          | 0/1108 [00:00<?, ? examples/s]

/home/sz38235/.local/lib/python3.11/site-packages/audiomentations/core/transforms_interface.py:62: UserWarning: Warning: input samples dtype is np.float64. Converting to np.float32
  warnings.warn(
/home/sz38235/.local/lib/python3.11/site-packages/audiomentations/core/transforms_interface.py:62: UserWarning: Warning: input samples dtype is np.float64. Converting to np.float32
  warnings.warn(


In [10]:
dataset["test"] = dataset["test"].map(augment_dataset)

Map:   0%|          | 0/278 [00:00<?, ? examples/s]

In [11]:
def prepare_dataset(batch):
    # load and resample audio data from 48 to 16kHz
    audio = batch["audio"]

    # compute log-Mel input features from input audio array 
    batch["input_features"] = feature_extractor(
        audio["array"], sampling_rate=audio["sampling_rate"]).input_features[0]

    # encode target text to label ids 
    batch["labels"] = tokenizer(batch["transcription"], max_length=225, truncation=True).input_ids
    return batch


In [12]:
dataset["train"] = dataset["train"].map(prepare_dataset)


Map:   0%|          | 0/1108 [00:00<?, ? examples/s]

2024-03-07 08:58:52.624068: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-07 08:58:52.624143: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-07 08:58:52.624926: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-07 08:58:52.628625: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-03-07 08:58:53.614848: W tensorflow/compiler/tf2

In [13]:
dataset["test"] = dataset["test"].map(prepare_dataset)

Map:   0%|          | 0/278 [00:00<?, ? examples/s]

In [14]:
dataset

DatasetDict({
    train: Dataset({
        features: ['audio', 'transcription', 'input_features', 'labels'],
        num_rows: 1108
    })
    test: Dataset({
        features: ['audio', 'transcription', 'input_features', 'labels'],
        num_rows: 278
    })
})

In [15]:
dataset['train'][0]

{'audio': {'path': None,
  'array': array([-0.00024414, -0.00018311,  0.        , ..., -0.00109863,
         -0.00119019,  0.        ]),
  'sampling_rate': 16000},
 'transcription': "Quel go imparà a- Čr- in- de Črnja, la roba migliore che go imparà là per tuta la vita, non esisti situazion ch- iriso- irisolvibile, non esisti, neanche una. Tuto se risolvi. Tuto. E il me ga imparà @ 'sto capo che xe mato, però xe bravissimo, sempre gaver tre-quatro @ piani.",
 'input_features': [[-0.3950995206832886,
   -0.061792612075805664,
   -0.33650124073028564,
   -0.09052050113677979,
   -0.0459752082824707,
   -0.04939854145050049,
   -0.22290253639221191,
   -0.10397005081176758,
   0.03906369209289551,
   -0.04826807975769043,
   -0.015499472618103027,
   -0.11104631423950195,
   -0.059494733810424805,
   -0.27508044242858887,
   -0.20180094242095947,
   -0.2960270643234253,
   -0.05422341823577881,
   -0.01742267608642578,
   -0.13349664211273193,
   -0.31698763370513916,
   -0.13240206241607

In [17]:
# save dataset

dataset.save_to_disk("/work/jh2lab/elic_model/ivn_dataset_preprocessed")

Saving the dataset (0/6 shards):   0%|          | 0/1108 [00:00<?, ? examples/s]

Saving the dataset (0/2 shards):   0%|          | 0/278 [00:00<?, ? examples/s]

# load dataset from presaved

In [2]:
from transformers import WhisperFeatureExtractor

#feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-large-v3")


feature_extractor = WhisperFeatureExtractor.from_pretrained("openai/whisper-large-v3", language="italian", task="transcribe")
       

In [3]:
from transformers import WhisperTokenizer

tokenizer = WhisperTokenizer.from_pretrained("openai/whisper-large-v3", language="italian", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [4]:
from transformers import WhisperProcessor

processor = WhisperProcessor.from_pretrained("openai/whisper-large-v3", language="italian", task="transcribe")


Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [5]:
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

In [6]:
from datasets import load_from_disk
dataset = load_from_disk("/work/jh2lab/elic_model/ivn_dataset_preprocessed")

In [6]:
dataset['train'][0]

{'audio': {'path': None,
  'array': array([-0.00024414, -0.00018311,  0.        , ..., -0.00109863,
         -0.00119019,  0.        ]),
  'sampling_rate': 16000},
 'transcription': "Quel go imparà a- Čr- in- de Črnja, la roba migliore che go imparà là per tuta la vita, non esisti situazion ch- iriso- irisolvibile, non esisti, neanche una. Tuto se risolvi. Tuto. E il me ga imparà @ 'sto capo che xe mato, però xe bravissimo, sempre gaver tre-quatro @ piani.",
 'input_features': [[-0.3950995206832886,
   -0.061792612075805664,
   -0.33650124073028564,
   -0.09052050113677979,
   -0.0459752082824707,
   -0.04939854145050049,
   -0.22290253639221191,
   -0.10397005081176758,
   0.03906369209289551,
   -0.04826807975769043,
   -0.015499472618103027,
   -0.11104631423950195,
   -0.059494733810424805,
   -0.27508044242858887,
   -0.20180094242095947,
   -0.2960270643234253,
   -0.05422341823577881,
   -0.01742267608642578,
   -0.13349664211273193,
   -0.31698763370513916,
   -0.13240206241607

In [7]:
#import wandb
import pandas as pd

In [8]:
import torch

from dataclasses import dataclass
from typing import Any, Dict, List, Union

@dataclass
class DataCollatorSpeechSeq2SeqWithPadding:
    processor: Any

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lengths and need different padding methods
        # first treat the audio inputs by simply returning torch tensors
        input_features = [{"input_features": feature["input_features"]} for feature in features]
        batch = self.processor.feature_extractor.pad(input_features, return_tensors="pt")

        # get the tokenized label sequences
        label_features = [{"input_ids": feature["labels"]} for feature in features]
        # pad the labels to max length
        labels_batch = self.processor.tokenizer.pad(label_features, return_tensors="pt")

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        # if bos token is appended in previous tokenization step,
        # cut bos token here as it's append later anyways
        if (labels[:, 0] == self.processor.tokenizer.bos_token_id).all().cpu().item():
            labels = labels[:, 1:]

        batch["labels"] = labels

        return batch


In [9]:
torch.cuda.empty_cache()

In [10]:
data_collator = DataCollatorSpeechSeq2SeqWithPadding(processor=processor)

In [11]:
import evaluate

metric = evaluate.load("wer")

2024-03-07 14:09:33.688916: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-07 14:09:33.688954: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-07 14:09:33.690543: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-07 14:09:33.699444: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-03-07 14:09:34.959870: W tensorflow/comp

In [12]:
def compute_metrics(pred):
    pred_ids = pred.predictions
    label_ids = pred.label_ids

    # replace -100 with the pad_token_id
    label_ids[label_ids == -100] = tokenizer.pad_token_id

    # we do not want to group tokens when computing the metrics
    pred_str = tokenizer.batch_decode(pred_ids, skip_special_tokens=True)
    label_str = tokenizer.batch_decode(label_ids, skip_special_tokens=True)

    wer = 100 * metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer}


In [13]:
from transformers import WhisperForConditionalGeneration

model = WhisperForConditionalGeneration.from_pretrained("openai/whisper-large-v3")


In [14]:
from huggingface_hub import notebook_login

notebook_login()

In [15]:
from transformers import Seq2SeqTrainingArguments

training_args = Seq2SeqTrainingArguments(
    output_dir="/work/jh2lab/elic_model/whisper-large-v3-ivn-v2",  # v2 change CUDA setting
    per_device_train_batch_size=16,
    gradient_accumulation_steps=1,  # increase by 2x for every 2x decrease in batch size
    learning_rate=1e-5,
    warmup_steps=500,
    max_steps=4000,
    gradient_checkpointing=True,
    fp16=True, # only on CPU error 
    evaluation_strategy="steps",
    per_device_eval_batch_size=8,
    predict_with_generate=True,
    generation_max_length=225,
    save_steps=1000,
    eval_steps=1000,
    logging_steps=25,
    report_to=["tensorboard"],
    load_best_model_at_end=True,
    metric_for_best_model="wer",
    greater_is_better=False,
    push_to_hub=False,
)

In [16]:
from transformers import Seq2SeqTrainer

trainer = Seq2SeqTrainer(
    args=training_args,
    model=model,
    train_dataset=dataset["train"],
    eval_dataset=dataset["test"],
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    tokenizer=processor.feature_extractor,
)

Detected kernel version 4.18.0, which is below the recommended minimum of 5.5.0; this can cause the process to hang. It is recommended to upgrade the kernel to the minimum version or higher.


In [ ]:
trainer.train()

/home/sz38235/.local/lib/python3.11/site-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
`use_cache = True` is incompatible with gradient checkpointing. Setting `use_cache = False`...


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 448, 'begin_suppress_tokens': [220, 50257]}
/home/sz38235/.local/lib/python3.11/site-packages/torch/utils/checkpoint.py:460: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transforme

In [ ]:
kwargs = {
    #"dataset_tags": "mozilla-foundation/common_voice_11_0",
    #"dataset": "Common Voice 11.0",  # a 'pretty' name for the training dataset
    "dataset_args": "config: ivn, split: test",
    "language": "ivn",
    #"model_name": "Whisper Small Hi - Sanchit Gandhi",  # a 'pretty' name for your model
    "finetuned_from": "openai/whisper-large-v3",
    "tasks": "automatic-speech-recognition",
    #"tags": "hf-asr-leaderboard",
}

In [ ]:
trainer.push_to_hub(**kwargs)

In [ ]:
tokenizer.save_pretrained("/work/jh2lab/elic_model/whisper-large-v3-ivn-v2") # add this to the folder, it is not auto saved

In [ ]:
trainer.push_to_hub("ninninz/whisper-large-v3-ivn-v2")